<a href="https://colab.research.google.com/github/vpkrishna/nlp/blob/main/Bert_Finbert_embeddings.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from google.colab import drive
drive.mount('/content/drive',force_remount=True)

Mounted at /content/drive


In [ ]:
%pip install dspy-ai

In [ ]:
import datasets
import openai
import os
import dspy


In [ ]:
%pip install sentence_transformers

In [ ]:
import pandas as pd
df = pd.read_csv('/content/drive/MyDrive/2Stanford/2nlp/Hybrid_Mkt_GPT_4_Theme_Industry_Keywords.csv')
trainsets = []
df_grouped = df.groupby('Theme_Name').agg({
    'Sub_Industry': ', '.join,
    'Keywords': ', '.join
}).reset_index()

In [ ]:
industry_embeddings=df_grouped['Theme_Name'].values.tolist()

## SEC Dataset

In [ ]:
# Load a specific year and split
year_2020_training_dataset = datasets.load_dataset("eloukas/edgar-corpus", "year_2020", split="train")

/usr/local/lib/python3.10/dist-packages/datasets/table.py:1421: FutureWarning: promote has been superseded by mode='default'.
  table = cls._concat_blocks(blocks, axis=0)


In [ ]:
year_2020_training_dataset.column_names

['filename',
 'cik',
 'year',
 'section_1',
 'section_1A',
 'section_1B',
 'section_2',
 'section_3',
 'section_4',
 'section_5',
 'section_6',
 'section_7',
 'section_7A',
 'section_8',
 'section_9',
 'section_9A',
 'section_9B',
 'section_10',
 'section_11',
 'section_12',
 'section_13',
 'section_14',
 'section_15']

In [ ]:
# Specify the columns you want to keep
columns_to_keep = ['filename', 'cik', 'year', 'section_1', 'section_7']

# Create a copy of the dataset with only the desired columns
subset_dataset = year_2020_training_dataset.remove_columns([col for col in year_2020_training_dataset.column_names if col not in columns_to_keep])

In [ ]:
subset_dataset=subset_dataset.to_pandas()

In [ ]:
%pip install sec-cik-mapper

In [ ]:
from sec_cik_mapper import StockMapper

In [ ]:
mapper=StockMapper()

In [ ]:

subset_dataset['cik'] = subset_dataset['cik'].str.zfill(10)
cik_to_ticker = mapper.cik_to_tickers
subset_dataset['ticker'] = subset_dataset['cik'].map(cik_to_ticker)
subset_dataset['ticker'] = subset_dataset['ticker'].apply(lambda x: list(x)[0] if isinstance(x, set) else x)
subset_dataset['ticker'] = subset_dataset['ticker'].fillna(subset_dataset['cik'])
subset_dataset['ticker']

0             CMTV
1             RNVA
2             DLPN
3             PAYX
4       0001490873
           ...    
5475          GRNF
5476    0001807594
5477           PAR
5478          NOTV
5479         BEEMW
Name: ticker, Length: 5480, dtype: object

In [ ]:
import json

# Assuming df is your DataFrame and json_file is your JSON file
with open('/content/drive/MyDrive/2Stanford/2nlp/project/companies_info.json', 'r') as f:
    data = json.load(f)

# Create a mapping from the 'cik' to 'Company Name'
cik_to_company = {cik: info['Company Name'] for cik, info in data.items()}

# Use the map function to replace the 'cik' values
subset_dataset['cik'] = subset_dataset['cik'].map(cik_to_company).fillna(subset_dataset['cik'])

In [ ]:
subset_dataset['section_1_7'] = subset_dataset.apply(lambda x: x['section_1'] + " " + x['section_7'], axis=1)

In [ ]:
subset_dataset.shape

(5480, 7)

In [ ]:
import torch
from sentence_transformers import SentenceTransformer

In [ ]:

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load a pre-trained BERT model
model = SentenceTransformer('bert-base-uncased', device=device)

In [ ]:

consolidated_industry_words=df_grouped['Theme_Name'].values.tolist()
industry_embeddings = model.encode(consolidated_industry_words, convert_to_tensor=True)


In [ ]:
from datasets import Dataset

# Convert the pandas DataFrame back to a Dataset object
subset_dataset = Dataset.from_pandas(subset_dataset)

In [ ]:
# Define a function for batch processing
def encode_batch(batch):
    return {'embeddings': model.encode(batch['section_1_7'], show_progress_bar=True)}

# Add embeddings to your dataset
subset_dataset = subset_dataset.map(encode_batch, batched=True, batch_size=32)




Map:   0%|          | 0/5480 [00:00<?, ? examples/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
import numpy as np
# Convert embeddings list to numpy array for efficient cosine similarity calculation
all_embeddings = np.array(subset_dataset['embeddings'])


In [ ]:
print(type(industry_embeddings))
print(industry_embeddings)
print(type(industry_embeddings))
print(industry_embeddings)

<class 'torch.Tensor'>
tensor([[ 0.2884,  0.1792,  0.1275,  ..., -0.2006,  0.0311,  0.1591],
        [-0.1826, -0.1605, -0.0396,  ..., -0.3076, -0.1650, -0.1689],
        [ 0.4020,  0.0887, -0.0660,  ..., -0.4271,  0.0152, -0.0662],
        ...,
        [ 0.6496, -0.0450,  0.0535,  ..., -0.0913,  0.2490,  0.2572],
        [ 0.4043,  0.1592,  0.1659,  ..., -0.2751,  0.2083, -0.0493],
        [ 0.3509, -0.0093, -0.1581,  ..., -0.1854, -0.2983, -0.1219]],
       device='cuda:0')
<class 'torch.Tensor'>
tensor([[ 0.2884,  0.1792,  0.1275,  ..., -0.2006,  0.0311,  0.1591],
        [-0.1826, -0.1605, -0.0396,  ..., -0.3076, -0.1650, -0.1689],
        [ 0.4020,  0.0887, -0.0660,  ..., -0.4271,  0.0152, -0.0662],
        ...,
        [ 0.6496, -0.0450,  0.0535,  ..., -0.0913,  0.2490,  0.2572],
        [ 0.4043,  0.1592,  0.1659,  ..., -0.2751,  0.2083, -0.0493],
        [ 0.3509, -0.0093, -0.1581,  ..., -0.1854, -0.2983, -0.1219]],
       device='cuda:0')


In [ ]:
from sklearn.metrics.pairwise import cosine_similarity

# Move tensors to CPU
industry_embeddings_cpu = industry_embeddings.cpu()
#all_embeddings_cpu = all_embeddings.cpu()

# Calculate cosine similarities between keyword embeddings and document embeddings
similarities = cosine_similarity(industry_embeddings_cpu, all_embeddings)

# Aggregate similarities - here, taking the max similarity score for each document across all keywords
max_similarities = similarities.max(axis=0)

# Sort documents by their aggregated similarity score
sorted_indices = max_similarities.argsort()[::-1]

In [ ]:
sorted_indices = max_similarities.argsort()[::-1]
ticker_codes=subset_dataset['ticker']
top_n = 1500  # Adjust based on how many top results you want

In [ ]:
similarities.shape

(25, 5480)

In [ ]:
consolidated_industry_words

['Aerospace & Defence',
 'Aging Population',
 'Autonomous Technology & Robotics',
 'Biotechnology',
 'Blockchain and Tech',
 'Clean Energy',
 'Cloud Computing',
 'Cybersecurity',
 'Data Center REITs & Digital Infrastructure',
 'Fintech Innovation',
 'Genomic Revolution',
 'Genomics & Biotechnology',
 'Hydrogen',
 'Internet of Things',
 'Lithium & Battery Tech',
 'Medical Devices ',
 'Next Generation Internet',
 'Renewable Energy Producers',
 'Robotics and Artificial Intelligence',
 'Semiconductor',
 'Solar',
 'Space Exploration & Innovation',
 'Telemedicine & Digital Health',
 'Video Games & Esports ',
 'Wind Energy']

In [ ]:
# Assuming 'cik_codes' and 'similarities' are correctly defined
top_n=1500
for index, industry_data in enumerate(consolidated_industry_words):
    print(f"Industry: {industry_data}")
    industry_similarities = similarities[index]
    sorted_doc_indices = np.argsort(industry_similarities)[::-1][:top_n]
    for doc_index in sorted_doc_indices:
        ticker_code = ticker_codes[doc_index]
        score = industry_similarities[doc_index]
        print(f"Ticker: {ticker_code}, Similarity Score: {score:.4f}")
    print("\n")

Streaming output truncated to the last 5000 lines.
Ticker: 0001829797, Similarity Score: 0.4677
Ticker: APEI, Similarity Score: 0.4676
Ticker: RPRX, Similarity Score: 0.4676
Ticker: SPT, Similarity Score: 0.4676
Ticker: 0000945764, Similarity Score: 0.4676
Ticker: OPK, Similarity Score: 0.4675
Ticker: 0001783317, Similarity Score: 0.4675
Ticker: PRKR, Similarity Score: 0.4675
Ticker: COHU, Similarity Score: 0.4675
Ticker: ALOT, Similarity Score: 0.4675
Ticker: DOV, Similarity Score: 0.4674
Ticker: TTGT, Similarity Score: 0.4674
Ticker: IT, Similarity Score: 0.4674
Ticker: APYX, Similarity Score: 0.4673
Ticker: 0000890547, Similarity Score: 0.4673
Ticker: 0000887921, Similarity Score: 0.4673
Ticker: XELA, Similarity Score: 0.4672
Ticker: SDGR, Similarity Score: 0.4672
Ticker: TGEN, Similarity Score: 0.4671
Ticker: PSIX, Similarity Score: 0.4670
Ticker: SRDX, Similarity Score: 0.4670
Ticker: 0000088790, Similarity Score: 0.4670
Ticker: OSIS, Similarity Score: 0.4670
Ticker: DCLT, Similar

In [ ]:
consolidated_industry_words_mapping=['Next Generation Internet','Genomic Revolution','Fintech Innovation','Space Exploration & Innovation','Autonomous Technology & Robotics',
                                     'Robotics and Artificial Intelligence','Blockchain and Tech','Cybersecurity','Cloud Computing','Lithium & Battery Tech',
                                      'Data Center REITs & Digital Infrastructure','Aging Population','Telemedicine & Digital Health','Semiconductor','Biotechnology',
                                      'Aerospace & Defence','Medical Devices','Genomics & Biotechnology','Hydrogen','Solar',
                                      'Renewable Energy Producers','Wind Energy','Video Games & Esports','Internet of Things','Clean Energy']
len(consolidated_industry_words_mapping)

25

In [ ]:
import os
import pandas as pd
import numpy as np

# Initialize counters
true_positive = 0
false_positive = 0
false_negative = 0

# Directory containing the files
directory = '/content/drive/MyDrive/2Stanford/2nlp/project/filesformapping'

# Get a list of all file names in the directory
file_names = sorted(os.listdir(directory))
top_n=250
# For each industry_data in consolidated_industry_words_mapping
for index, industry_data in enumerate(consolidated_industry_words_mapping):
    print(f"Industry: {industry_data}")

    # Get the ticker codes for the current industry
    industry_similarities = similarities[index]
    sorted_doc_indices = np.argsort(industry_similarities)[::-1][:top_n]
    industry_tickers = sorted([ticker_codes[doc_index] for doc_index in sorted_doc_indices])

    # Read the corresponding file
    file_path = os.path.join(directory, file_names[index])

    # Skip rows until 'ticker' or 'TICKER' column is found
    with open(file_path, 'r') as f:
        for i, line in enumerate(f):
            if 'ticker' in line.lower():
                skiprows = i
                break
    print(file_path)
    df = pd.read_csv(file_path, skiprows=skiprows,on_bad_lines='skip')

    # Check if the column name is 'ticker' or 'TICKER'
    ticker_column = 'ticker' if 'ticker' in df.columns else 'Ticker'

    # Get the ticker codes from the file
    file_tickers = sorted([x for x in set(df[ticker_column][:top_n]) if isinstance(x, str) and not (len(x.split(' ')[-1]) == 2)])

    print(industry_tickers)
    print(file_tickers)
    print(true_positive,set(industry_tickers) & set(file_tickers),len(set(industry_tickers) & set(file_tickers)))

    # Calculate true positives, false positives, and false negatives
    true_positive += len(set(industry_tickers) & set(file_tickers))
    false_negative += len(set(industry_tickers) - set(file_tickers))
    false_positive += len(set(file_tickers) - set(industry_tickers))

# Print the final counts
print(f"True Positives: {true_positive}")
print(f"False Positives: {false_positive}")
print(f"False Negatives: {false_negative}")

Industry: Next Generation Internet
/content/drive/MyDrive/2Stanford/2nlp/project/filesformapping/01_ARK_NEXT_GENERATION_INTERNET_ETF_ARKW_HOLDINGS.csv
['0000098752', '0000894329', '0000921864', '0000922869', '0001003509', '0001082027', '0001108967', '0001128250', '0001139552', '0001140096', '0001159408', '0001162387', '0001163321', '0001171040', '0001174821', '0001226006', '0001282663', '0001290098', '0001354371', '0001379404', '0001383094', '0001396730', '0001405332', '0001477336', '0001492632', '0001493611', '0001499357', '0001522616', '0001541451', '0001549785', '0001558013', '0001571237', '0001577311', '0001587497', '0001595710', '0001600823', '0001606104', '0001623916', '0001629069', '0001631406', '0001636513', '0001640775', '0001642727', '0001645731', '0001646924', '0001655591', '0001656047', '0001657889', '0001663645', '0001664682', '0001669374', '0001669990', '0001671212', '0001678507', '0001678740', '0001685022', '0001686277', '0001687374', '0001689417', '0001693368', '0001693

In [ ]:
set([3,4,7]) - set([1,2,3])

{4, 7}

In [ ]:
df=mapper.raw_dataframe
df.loc[df['CIK']==2015534]

CIK Ticker                      Name Exchange
10389  2015534    JCY  Jingcaoyuan Holdings Inc     None

In [ ]:
df['CIK']=df['CIK'].astype(int)

In [ ]:
df

CIK Ticker                             Name Exchange
0         1750    AIR                         Aar Corp     NYSE
1         1800    ABT              Abbott Laboratories     NYSE
2         1961   WDDD                       Worlds Inc      OTC
3         2098    ACU                 Acme United Corp     NYSE
4         2178     AE   Adams Resources & Energy, Inc.     NYSE
...        ...    ...                              ...      ...
10389  2015534    JCY         Jingcaoyuan Holdings Inc     None
10390  2016435   LXTM       Lei Xin Holdings Co., Ltd.     None
10391  2017302   MISN  Mission Space Acquisition Corp.     None
10392  2019103   SLSR           Solaris Resources Inc.     None
10393  2019103  SLSSF           Solaris Resources Inc.      OTC

[10394 rows x 4 columns]

In [ ]:
# Load a pre-trained BERT model
model = SentenceTransformer('ProsusAI/finbert', device=device)

consolidated_industry_words=df_grouped['Theme_Name'].values.tolist()
industry_embeddings = model.encode(consolidated_industry_words, convert_to_tensor=True)

# Define a function for batch processing
def encode_batch(batch):
    return {'embeddings': model.encode(batch['section_1_7'], show_progress_bar=True)}

# Add embeddings to your dataset
subset_dataset = subset_dataset.map(encode_batch, batched=True, batch_size=32)

import numpy as np
# Convert embeddings list to numpy array for efficient cosine similarity calculation
all_embeddings = np.array(subset_dataset['embeddings'])


from sklearn.metrics.pairwise import cosine_similarity

# Move tensors to CPU
industry_embeddings_cpu = industry_embeddings.cpu()
#all_embeddings_cpu = all_embeddings.cpu()

# Calculate cosine similarities between keyword embeddings and document embeddings
similarities = cosine_similarity(industry_embeddings_cpu, all_embeddings)

# Aggregate similarities - here, taking the max similarity score for each document across all keywords
max_similarities = similarities.max(axis=0)

# Sort documents by their aggregated similarity score
sorted_indices = max_similarities.argsort()[::-1]


sorted_indices = max_similarities.argsort()[::-1]
ticker_codes=subset_dataset['ticker']

# Assuming 'cik_codes' and 'similarities' are correctly defined
top_n=1500
for index, industry_data in enumerate(consolidated_industry_words):
    print(f"Industry: {industry_data}")
    industry_similarities = similarities[index]
    sorted_doc_indices = np.argsort(industry_similarities)[::-1][:top_n]
    for doc_index in sorted_doc_indices:
        ticker_code = ticker_codes[doc_index]
        score = industry_similarities[doc_index]
        print(f"Ticker: {ticker_code}, Similarity Score: {score:.4f}")
    print("\n")

Map:   0%|          | 0/5480 [00:00<?, ? examples/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Streaming output truncated to the last 5000 lines.
Ticker: COLM, Similarity Score: 0.7371
Ticker: AJIA, Similarity Score: 0.7370
Ticker: RENO, Similarity Score: 0.7370
Ticker: ADNT, Similarity Score: 0.7370
Ticker: 0001109448, Similarity Score: 0.7369
Ticker: SLNG, Similarity Score: 0.7369
Ticker: BLNK, Similarity Score: 0.7369
Ticker: NXGL, Similarity Score: 0.7368
Ticker: SBCF, Similarity Score: 0.7368
Ticker: CLOQ, Similarity Score: 0.7368
Ticker: ACGLN, Similarity Score: 0.7367
Ticker: BXMT, Similarity Score: 0.7367
Ticker: 0001002517, Similarity Score: 0.7367
Ticker: SRI, Similarity Score: 0.7367
Ticker: 0000216877, Similarity Score: 0.7367
Ticker: LVVR, Similarity Score: 0.7367
Ticker: DDS, Similarity Score: 0.7366
Ticker: 0001418100, Similarity Score: 0.7366
Ticker: VICR, Similarity Score: 0.7366
Ticker: NHHS, Similarity Score: 0.7366
Ticker: MPWR, Similarity Score: 0.7365
Ticker: DOMO, Similarity Score: 0.7364
Ticker: UNAM, Similarity Score: 0.7364
Ticker: 0001724001, Similarit

In [ ]:
on_bad_lines='skip'

In [ ]:
consolidated_industry_words_mapping=['Next Generation Internet','Genomic Revolution','Fintech Innovation','Space Exploration & Innovation','Autonomous Technology & Robotics',
                                     'Robotics and Artificial Intelligence','Blockchain and Tech','Cybersecurity','Cloud Computing','Lithium & Battery Tech',
                                      'Data Center REITs & Digital Infrastructure','Aging Population','Telemedicine & Digital Health','Semiconductor','Biotechnology',
                                      'Aerospace & Defence','Medical Devices','Genomics & Biotechnology','Hydrogen','Solar',
                                      'Renewable Energy Producers','Wind Energy','Video Games & Esports','Internet of Things','Clean Energy']
len(consolidated_industry_words_mapping)

25

In [ ]:
# Initialize counters
true_positive = 0
false_positive = 0
false_negative = 0

# Directory containing the files
directory = '/content/drive/MyDrive/2Stanford/2nlp/project/filesformapping'

# Get a list of all file names in the directory
file_names = sorted(os.listdir(directory))
top_n=250
# For each industry_data in consolidated_industry_words_mapping
for index, industry_data in enumerate(consolidated_industry_words_mapping):
    print(f"Industry: {industry_data}")

    # Get the ticker codes for the current industry
    industry_similarities = similarities[index]
    sorted_doc_indices = np.argsort(industry_similarities)[::-1][:top_n]
    industry_tickers = sorted([ticker_codes[doc_index] for doc_index in sorted_doc_indices])

    # Read the corresponding file
    file_path = os.path.join(directory, file_names[index])

    # Skip rows until 'ticker' or 'TICKER' column is found
    with open(file_path, 'r') as f:
        for i, line in enumerate(f):
            if 'ticker' in line.lower():
                skiprows = i
                break
    print(file_path)
    df = pd.read_csv(file_path, skiprows=skiprows,on_bad_lines='skip')

    # Check if the column name is 'ticker' or 'TICKER'
    ticker_column = 'ticker' if 'ticker' in df.columns else 'Ticker'

    # Get the ticker codes from the file
    ## file_tickers = sorted([x for x in set(df[ticker_column][:top_n]) if isinstance(x, str)])
    file_tickers = sorted([x for x in set(df[ticker_column][:top_n]) if isinstance(x, str) and not (len(x.split(' ')[-1]) == 2)])

    print(industry_tickers)
    print(file_tickers)
    print(false_negative,true_positive,set(industry_tickers) & set(file_tickers),len(set(industry_tickers) & set(file_tickers)))

    # Calculate true positives, false positives, and false negatives
    true_positive += len(set(industry_tickers) & set(file_tickers))
    false_negative += len(set(industry_tickers) - set(file_tickers))
    false_positive += len(set(file_tickers) - set(industry_tickers))

# Print the final counts
print(f"True Positives: {true_positive}")
print(f"False Positives: {false_positive}")
print(f"False Negatives: {false_negative}")

Industry: Next Generation Internet
/content/drive/MyDrive/2Stanford/2nlp/project/filesformapping/01_ARK_NEXT_GENERATION_INTERNET_ETF_ARKW_HOLDINGS.csv
['0000003153', '0000007039', '0000007286', '0000017797', '0000020290', '0000021510', '0000027673', '0000030371', '0000052485', '0000055387', '0000060549', '0000074145', '0000075340', '0000078460', '0000081020', '0000081033', '0000096271', '0000098752', '0000317187', '0000701869', '0000731288', '0000743316', '0000743988', '0000808450', '0000815917', '0000865058', '0000898770', '0000912752', '0000922612', '0000931182', '0001011432', '0001011659', '0001029831', '0001045309', '0001068148', '0001082923', '0001084580', '0001094093', '0001108967', '0001144519', '0001158659', '0001160661', '0001389034', '0001438731', '0001449488', '0001466538', '0001494877', '0001518339', '0001585101', '0001587246', '0001599489', '0001740695', '0001781870', 'A', 'ACFN', 'ACNT', 'AEE', 'AILLM', 'AIRTP', 'AIT', 'ALGN', 'ALNT', 'ALOT', 'ALV', 'AOXY', 'APH', 'APT', 